In [81]:
import pandas as pd
import geopandas as gpd
import folium
from folium.plugins import Fullscreen
#import seaborn
import holoviews
import hvplot
import panel as pn
import matplotlib as plt
%matplotlib inline
pn.extension()
#from panel import theme
#from IPython.display import display
#import os

In [3]:
stats = pd.read_csv("data/stats_merged.csv",encoding="utf-8") # social statistics
admin = gpd.read_file("data/Stadtteile_Hamburg.shp",crs="EPSG:25832") # boundary dataset 
#combined_indicators = pd.read_csv("data/combined_indicators.csv",encoding="utf-8") # social statistics


In [4]:
stats.drop(columns=['geometry_x','geometry_y', 'geometry','bezirk_nam_x', 'bezirk_nam_y', 'ZONE_CODE', 'COUNT', 'AREA', 'MIN','MAX', 'RANGE'], inplace=True);


In [5]:
admin_stats = pd.merge(admin, stats, left_index=True, right_index=True) 


In [ ]:
admin_stats.columns

In [29]:
"""-----Function to add a status column  --- """

def add_status_column(df, perc_col): #The function will be used for all of the different indicators)
    """The function adds a text column to the dataframe. The value of the text column is assigned based
        on the values of the classified "_percentile column"

    Parameters: 
        df : dataframe used for the classification
        perc_col: Column used to assign te the text values: NEEDS to be a categorial variable, resulting from the 
        "percentile functions" Has to take the classified column:result of func percentile as input
        
    Returns:
        A dataframe with a new column called "status" containing strings with the values from "very low" to "very high"
        Assignes the names based on the values in the perc_col
        
    Apply the functin:
        Example: add_status_column(dataframe, 'columnName') # 

    """
    df['status'] = ['very low' if x == 0 else  #creates the new column "status and then adds text description to the corresponding value"
                   'low' if x == 1 else
                   'medium' if x == 2 else
                   'high' if x == 3 else
                   'very high' for x in df[perc_col]]

    return df.head()

In [30]:
add_status_column(admin_stats, 'combined_indicators_percentile')

OBJECTID_x bezirk_x     bezirk_nam      stadtteil__x stadttei_1_x   
0           1        1  Hamburg-Mitte  Hamburg-Altstadt        02101  \
1           2        1  Hamburg-Mitte         HafenCity        02102   
2           3        1  Hamburg-Mitte          Neustadt        02103   
3           4        1  Hamburg-Mitte         St. Pauli        02104   
4           5        1  Hamburg-Mitte         St. Georg        02105   

  stadttei_2_x  SHAPE_Leng_x  SHAPE_Area_x   
0          101   9028.180532  3.676562e+06  \
1          102  13902.691334  6.860720e+06   
2          103  11133.923114  6.395226e+06   
3          104  15968.675123  6.343533e+06   
4          105   9795.650670  5.155061e+06   

                                            geometry         stadtteil  ...   
0  POLYGON ((1113865.821 7085107.333, 1113978.324...  Hamburg-Altstadt  ...  \
1  POLYGON ((1113043.882 7082944.386, 1112901.932...         HafenCity  ...   
2  POLYGON ((1112508.476 7085835.161, 1112319.283...          Neustadt  ...   
3  POLYGON ((1109116.549 7084327.397, 1109001.027...               NaN  ...   
4  POLYGON ((1114563.830 7085359.663, 1114541.839...               NaN  ...   

      MEDIAN      PCT90  MEDIAN_percentile status_temp_b  env_multiple_burden   
0  31.370575  32.559357                  4     very high                  1.0  \
1  28.833740  31.015308                  1           low                  9.0   
2  30.601608  32.068347                  3          high                  4.0   
3  31.357025  32.999854                  4     very high                  7.0   
4  31.347992  32.971094                  4     very high                 12.0   

   combined_indicators  env_multiple_burden_percentile   
0                  4.0                             0.0  \
1                 10.0                             4.0   
2                  7.0                             1.0   
3                  7.0                             2.0   
4                 16.0                             4.0   

   combined_indicators_percentile sum_socials     status  
0                             0.0        25.9   very low  
1                             3.0        32.9       high  
2                             1.0        25.0        low  
3                             1.0         NaN        low  
4                             4.0         NaN  very high  

[5 rows x 48 columns]

In [ ]:
admin_stats.columns

In [80]:
#gdf_reproj = combined_indicators.to_crs(epsg=25832)    # Reprojects the GeoDataFrame to EPSG 25832
def f(x):
    return x * x
pn.interact(f, x=10)

Column
    [0] Column
        [0] IntSlider(end=30, name='x', start=-10, value=10)
    [1] Row
        [0] Str(int, name='interactive00795')

In [67]:
stats_to_plot = admin_stats[['district','geometry','qt_soc_stats','status' ,'%unemployed', '%social_benefits','%social_housing', 'weighted_area_percentile', 'z_area_per_inhbt_percentile','MEDIAN_percentile','env_multiple_burden_percentile', 'combined_indicators_percentile']]

In [68]:
stats_to_plot_rename=stats_to_plot.rename(columns={"district":"District","weighted_area_percentile":"Noise Pollution","z_area_per_inhbt_percentile":"Green Area Supply ","MEDIAN_percentile":"Thermal Burden","env_multiple_burden_percentile":"Combined Environmental Burden" , "combined_indicators_percentile":"Combined Indicators", "status":"Integrated Environmental & Social Status Index","qt_soc_stats":"Social Status"})

In [69]:
stats_to_plot_rename.head()
stats_to_plot_rename.dropna(inplace=True);
stats_to_plot_reproj=stats_to_plot_rename.to_crs(epsg=25832)

In [70]:
stats_to_plot_reproj.crs

<Projected CRS: EPSG:25832>
Name: ETRS89 / UTM zone 32N
Axis Info [cartesian]:
- E[east]: Easting (metre)
- N[north]: Northing (metre)
Area of Use:
- name: Europe between 6°E and 12°E: Austria; Belgium; Denmark - onshore and offshore; Germany - onshore and offshore; Norway including - onshore and offshore; Spain - offshore.
- bounds: (6.0, 38.76, 12.01, 84.33)
Coordinate Operation:
- name: UTM zone 32N
- method: Transverse Mercator
Datum: European Terrestrial Reference System 1989 ensemble
- Ellipsoid: GRS 1980
- Prime Meridian: Greenwich

In [84]:
m = folium.Map(location=[53.55, 9.99], zoom_start=10)

m = stats_to_plot_reproj.explore('Integrated Environmental & Social Status Index', # show the Distance column
                   cmap='plasma', # use the 'plasma' colormap from matplotlib
                  )

folium.TileLayer("OpenStreetMap").add_to(m)
folium.TileLayer("Stamen Terrain").add_to(m)
folium.LayerControl().add_to(m)



In [85]:

m


In [78]:
year_slider = pn.widgets.IntSlider(name='Year slider', start=1750, end=2020, step=5, value=1850)
year_slider

IntSlider(end=2020, name='Year slider', start=1750, step=5, value=1850)

In [ ]:

dashboad_title ="EJ"
dshboard_description="a dashboard showing"

#dashboard = (dashboard_title, dashboard_description, rd_param,)

# Show the Panel layout
